In [30]:
from gensim import corpora, models, similarities
import gensim

In [31]:
import json 
import gzip 
#from StringIO import StringIO
import urllib.request
import requests, zipfile, io
import re

def parse(url): 
    if re.match("^http", url):
        r = requests.get(url)
        g = gzip.open(io.BytesIO(r.content))
    else:
        g = gzip.open(url, 'r') 
    for l in g:
        yield eval(l)

import json 
import gzip 
def parse(url): 
    g = gzip.open(url, 'r') 
    for l in g: 
        yield eval(l)

In [32]:
import gensim
import nltk
stoplist = nltk.corpus.stopwords.words('english')
lemma = nltk.stem.wordnet.WordNetLemmatizer()

def myReviews(review_files_urls, catFilter = None, asin = None, concatenate = False, max_count = None):
    preprocess_reviewText = []
    for url in review_files_urls:
        print("Processing url: " + url)
        review_item_iterator = iter(parse(url))
        it = 0
        conc_count = 0
        for review_item in review_item_iterator:
            it += 1
            if (max_count is not None) and (it > max_count):
                return
        #for it in range(1000000):
            if it%100000==0:
                print("it="+str(it))

            reviewText = review_item["reviewText"]
            label = review_item["asin"] + "_" + review_item["reviewerID"] 
            preprocess_reviewText_i = gensim.utils.simple_preprocess(reviewText)
            preprocess_reviewText_i = [lemma.lemmatize(word) for word in preprocess_reviewText_i if word not in stoplist]


            #yield gensim.models.doc2vec.LabeledSentence(words=preprocess_reviewText, tags=[label])
            if (catFilter == None or (catFilter in review_item["categories"])) and (asin == None or (asin == review_item["asin"])):
                if concatenate==False:
                    yield preprocess_reviewText_i
                else:
                    conc_count += 1
                    preprocess_reviewText.extend(preprocess_reviewText_i)
                    print("Concatenated count: "+str(conc_count))
    if concatenate == True:
        print("Return the final text with length: "+str(len(preprocess_reviewText)))
        print(preprocess_reviewText)
        yield preprocess_reviewText

#base_url = "http://snap.stanford.edu/data/amazon/productGraph/categoryFiles/"
base_url = "/media/mister/ntfs/Rainer/y2buy/download/amazon_reviews_96_14/"

from bs4 import BeautifulSoup
import urllib.request


html = urllib.request.urlopen("http://snap.stanford.edu/data/amazon/productGraph/categoryFiles/")
soup = BeautifulSoup(html, 'html.parser')
#print(soup.prettify())
all_html_links = soup.find_all('a')
review_file_names = [links["href"] for links in all_html_links if re.match("^review.*[^_5|_10].json.gz$", links["href"])]

In [33]:
from os import listdir
from os.path import isfile, join
import re
base_url = "/media/mister/ntfs/Rainer/y2buy/download/amazon_reviews_96_14/"
onlyfiles = [f for f in listdir(base_url) if isfile(join(base_url, f))]
review_file_names = [file for file in onlyfiles if re.match("^review.*[^_5|_10].json.gz$", file)]

for links in all_html_links:
    if re.match("^review.*[^_5|_10].json.gz$", links["href"]):
        print(links["href"])

In [34]:


review_file_names= ["reviews_Books_10.json.gz" if file_name =="reviews_Books.json.gz" else file_name for file_name in review_file_names]
print(review_file_names)
review_file_urls = [base_url + review_file_name for review_file_name in review_file_names]
#print(review_file_urls)

['reviews_All_Electronics.json.gz', 'reviews_Blues.json.gz', 'reviews_Christian.json.gz', 'reviews_Electronics.json.gz', 'reviews_Health_and_Personal_Care.json.gz', 'reviews_RandB.json.gz', 'reviews_All_Beauty.json.gz', 'reviews_All_Credit_Cards.json.gz', 'reviews_Alternative_Rock.json.gz', 'reviews_Amazon_Coins.json.gz', 'reviews_Amazon_Fashion.json.gz', 'reviews_Amazon_Fire_TV.json.gz', 'reviews_Amazon_Instant_Video.json.gz', 'reviews_Appliances.json.gz', 'reviews_Appstore_for_Android.json.gz', 'reviews_Apps_for_Android.json.gz', 'reviews_Arts_Crafts_and_Sewing.json.gz', 'reviews_Automotive.json.gz', 'reviews_Baby.json.gz', 'reviews_Baby_Products.json.gz', 'reviews_Beauty.json.gz', 'reviews_Broadway_and_Vocalists.json.gz', 'reviews_Buy_a_Kindle.json.gz', 'reviews_Camera_and_Photo.json.gz', 'reviews_Car_Electronics.json.gz', 'reviews_Celebrate_your_Birthday_with_Nickelodeon.json.gz', 'reviews_Cell_Phones_and_Accessories.json.gz', "reviews_Children's_Music.json.gz", 'reviews_Classical.

In [35]:
  
import os
dictionaryFileName = '../../download/word2vec/reviews_all.dict'
if os.path.isfile(dictionaryFileName)==False:
    #dictionary = corpora.Dictionary(myReviews("Cell Phones"))
    dictionary = corpora.Dictionary()
    for review_file_url in review_file_urls:
        dictionary.add_documents(myReviews([review_file_url],max_count = 1000000))
        from six import iteritems
        once_ids = [tokenid for tokenid, docfreq in iteritems(dictionary.dfs) if docfreq == 1]
        dictionary.filter_tokens(once_ids)  # remove stop words and words that appear only once
        dictionary.compactify()  # remove gaps in id sequence after words that were removed
        print(dictionary)
    dictionary.save(dictionaryFileName)  # store the dictionary, for future reference
else:
    dictionary = corpora.Dictionary.load(dictionaryFileName)




    
import os
dictionaryFileName = '../../download/word2vec/reviews_all.dict'
if os.path.isfile(dictionaryFileName)==False:
    #dictionary = corpora.Dictionary(myReviews("Cell Phones"))
    dictionary = corpora.Dictionary(myReviews(review_file_urls))
    from six import iteritems
    once_ids = [tokenid for tokenid, docfreq in iteritems(dictionary.dfs) if docfreq == 1]
    dictionary.filter_tokens(once_ids)  # remove stop words and words that appear only once
    dictionary.compactify()  # remove gaps in id sequence after words that were removed
    dictionary.save(dictionaryFileName)  # store the dictionary, for future reference
else:
    dictionary = corpora.Dictionary.load(dictionaryFileName)

print(dictionary)

In [36]:
def myCorpus(review_file_urls, catFilter = None, asin = None, concatenate = False, max_count = None):
    for review in myReviews(review_file_urls,catFilter,asin,concatenate,max_count):
    # assume there's one document per line, tokens separated by whitespace
        yield dictionary.doc2bow(review)

In [37]:
import os
tfidfFileName ='../../download/word2vec/reviews_all_corpus.tfidf'
if os.path.isfile(tfidfFileName)==False:
    #tfidf = models.TfidfModel(myCorpus("Cell Phones"))
    tfidf = models.TfidfModel(myCorpus(review_file_urls,max_count = 1000000))
    tfidf.save(tfidfFileName)
else:
    tfidf = models.TfidfModel.load(tfidfFileName)

print(tfidf)

TfidfModel(num_docs=1093393, num_nnz=41632789)


In [40]:
import pickle

tfidf_document_FileName ='../../download/word2vec/reviews_cell_phones_review.tfidf'
if os.path.isfile(tfidf_document_FileName)==False:
    document = next(myCorpus(review_file_urls = ['../../download/word2vec/reviews_Cell_Phones_and_Accessories_w_Cat.json.gz'], catFilter="Cell Phones",concatenate=True))
    document_tfidf = tfidf[document]  
    pickle.dump(document_tfidf, open(tfidf_document_FileName, 'wb'))
else:
    document_tfidf = pickle.load( open( tfidf_document_FileName, "rb" ) )
    
    


Processing url: ../../download/word2vec/reviews_Cell_Phones_and_Accessories_w_Cat.json.gz
Concatenated count: 1
Concatenated count: 2
Concatenated count: 3
Concatenated count: 4
Concatenated count: 5
Concatenated count: 6
Concatenated count: 7
Concatenated count: 8
Concatenated count: 9
Concatenated count: 10
Concatenated count: 11
Concatenated count: 12
Concatenated count: 13
Concatenated count: 14
Concatenated count: 15
Concatenated count: 16
Concatenated count: 17
Concatenated count: 18
Concatenated count: 19
Concatenated count: 20
Concatenated count: 21
Concatenated count: 22
Concatenated count: 23
Concatenated count: 24
Concatenated count: 25
Concatenated count: 26
Concatenated count: 27
Concatenated count: 28
Concatenated count: 29
Concatenated count: 30
Concatenated count: 31
Concatenated count: 32
Concatenated count: 33
Concatenated count: 34
Concatenated count: 35
Concatenated count: 36
Concatenated count: 37
Concatenated count: 38
Concatenated count: 39
Concatenated count: 40

Concatenated count: 381
Concatenated count: 382
Concatenated count: 383
Concatenated count: 384
Concatenated count: 385
Concatenated count: 386
Concatenated count: 387
Concatenated count: 388
Concatenated count: 389
Concatenated count: 390
Concatenated count: 391
Concatenated count: 392
Concatenated count: 393
Concatenated count: 394
Concatenated count: 395
Concatenated count: 396
Concatenated count: 397
Concatenated count: 398
Concatenated count: 399
Concatenated count: 400
Concatenated count: 401
Concatenated count: 402
Concatenated count: 403
Concatenated count: 404
Concatenated count: 405
Concatenated count: 406
Concatenated count: 407
Concatenated count: 408
Concatenated count: 409
Concatenated count: 410
Concatenated count: 411
Concatenated count: 412
Concatenated count: 413
Concatenated count: 414
Concatenated count: 415
Concatenated count: 416
Concatenated count: 417
Concatenated count: 418
Concatenated count: 419
Concatenated count: 420
Concatenated count: 421
Concatenated cou

Concatenated count: 831
Concatenated count: 832
Concatenated count: 833
Concatenated count: 834
Concatenated count: 835
Concatenated count: 836
Concatenated count: 837
Concatenated count: 838
Concatenated count: 839
Concatenated count: 840
Concatenated count: 841
Concatenated count: 842
Concatenated count: 843
Concatenated count: 844
Concatenated count: 845
Concatenated count: 846
Concatenated count: 847
Concatenated count: 848
Concatenated count: 849
Concatenated count: 850
Concatenated count: 851
Concatenated count: 852
Concatenated count: 853
Concatenated count: 854
Concatenated count: 855
Concatenated count: 856
Concatenated count: 857
Concatenated count: 858
Concatenated count: 859
Concatenated count: 860
Concatenated count: 861
Concatenated count: 862
Concatenated count: 863
Concatenated count: 864
Concatenated count: 865
Concatenated count: 866
Concatenated count: 867
Concatenated count: 868
Concatenated count: 869
Concatenated count: 870
Concatenated count: 871
Concatenated cou

Concatenated count: 1170
Concatenated count: 1171
Concatenated count: 1172
Concatenated count: 1173
Concatenated count: 1174
Concatenated count: 1175
Concatenated count: 1176
Concatenated count: 1177
Concatenated count: 1178
Concatenated count: 1179
Concatenated count: 1180
Concatenated count: 1181
Concatenated count: 1182
Concatenated count: 1183
Concatenated count: 1184
Concatenated count: 1185
Concatenated count: 1186
Concatenated count: 1187
Concatenated count: 1188
Concatenated count: 1189
Concatenated count: 1190
Concatenated count: 1191
Concatenated count: 1192
Concatenated count: 1193
Concatenated count: 1194
Concatenated count: 1195
Concatenated count: 1196
Concatenated count: 1197
Concatenated count: 1198
Concatenated count: 1199
Concatenated count: 1200
Concatenated count: 1201
Concatenated count: 1202
Concatenated count: 1203
Concatenated count: 1204
Concatenated count: 1205
Concatenated count: 1206
Concatenated count: 1207
Concatenated count: 1208
Concatenated count: 1209


Concatenated count: 1583
Concatenated count: 1584
Concatenated count: 1585
Concatenated count: 1586
Concatenated count: 1587
Concatenated count: 1588
Concatenated count: 1589
Concatenated count: 1590
Concatenated count: 1591
Concatenated count: 1592
Concatenated count: 1593
Concatenated count: 1594
Concatenated count: 1595
Concatenated count: 1596
Concatenated count: 1597
Concatenated count: 1598
Concatenated count: 1599
Concatenated count: 1600
Concatenated count: 1601
Concatenated count: 1602
Concatenated count: 1603
Concatenated count: 1604
Concatenated count: 1605
Concatenated count: 1606
Concatenated count: 1607
Concatenated count: 1608
Concatenated count: 1609
Concatenated count: 1610
Concatenated count: 1611
Concatenated count: 1612
Concatenated count: 1613
Concatenated count: 1614
Concatenated count: 1615
Concatenated count: 1616
Concatenated count: 1617
Concatenated count: 1618
Concatenated count: 1619
Concatenated count: 1620
Concatenated count: 1621
Concatenated count: 1622


...

Concatenated count: 158515
Concatenated count: 158516
Concatenated count: 158517
Concatenated count: 158518
Concatenated count: 158519
Concatenated count: 158520
Concatenated count: 158521
Concatenated count: 158522
Concatenated count: 158523
Concatenated count: 158524
Concatenated count: 158525
Concatenated count: 158526
Concatenated count: 158527
Concatenated count: 158528
Concatenated count: 158529
Concatenated count: 158530
Concatenated count: 158531
Concatenated count: 158532
Concatenated count: 158533
Concatenated count: 158534
Concatenated count: 158535
Concatenated count: 158536
Concatenated count: 158537
Concatenated count: 158538
Concatenated count: 158539
Concatenated count: 158540
Concatenated count: 158541
Concatenated count: 158542
Concatenated count: 158543
Concatenated count: 158544
Concatenated count: 158545
Concatenated count: 158546
Concatenated count: 158547
Concatenated count: 158548
Concatenated count: 158549
Concatenated count: 158550
Concatenated count: 158551
C

Concatenated count: 158871
Concatenated count: 158872
Concatenated count: 158873
Concatenated count: 158874
Concatenated count: 158875
Concatenated count: 158876
Concatenated count: 158877
Concatenated count: 158878
Concatenated count: 158879
Concatenated count: 158880
Concatenated count: 158881
Concatenated count: 158882
Concatenated count: 158883
Concatenated count: 158884
Concatenated count: 158885
Concatenated count: 158886
Concatenated count: 158887
Concatenated count: 158888
Concatenated count: 158889
Concatenated count: 158890
Concatenated count: 158891
Concatenated count: 158892
Concatenated count: 158893
Concatenated count: 158894
Concatenated count: 158895
Concatenated count: 158896
Concatenated count: 158897
Concatenated count: 158898
Concatenated count: 158899
Concatenated count: 158900
Concatenated count: 158901
Concatenated count: 158902
Concatenated count: 158903
Concatenated count: 158904
Concatenated count: 158905
Concatenated count: 158906
Concatenated count: 158907
C

Concatenated count: 159219
Concatenated count: 159220
Concatenated count: 159221
Concatenated count: 159222
Concatenated count: 159223
Concatenated count: 159224
Concatenated count: 159225
Concatenated count: 159226
Concatenated count: 159227
Concatenated count: 159228
Concatenated count: 159229
Concatenated count: 159230
Concatenated count: 159231
Concatenated count: 159232
Concatenated count: 159233
Concatenated count: 159234
Concatenated count: 159235
Concatenated count: 159236
Concatenated count: 159237
Concatenated count: 159238
Concatenated count: 159239
Concatenated count: 159240
Concatenated count: 159241
Concatenated count: 159242
Concatenated count: 159243
Concatenated count: 159244
Concatenated count: 159245
Concatenated count: 159246
Concatenated count: 159247
Concatenated count: 159248
Concatenated count: 159249
Concatenated count: 159250
Concatenated count: 159251
Concatenated count: 159252
Concatenated count: 159253
Concatenated count: 159254
Concatenated count: 159255
C

Concatenated count: 159528
Concatenated count: 159529
Concatenated count: 159530
Concatenated count: 159531
Concatenated count: 159532
Concatenated count: 159533
Concatenated count: 159534
Concatenated count: 159535
Concatenated count: 159536
Concatenated count: 159537
Concatenated count: 159538
Concatenated count: 159539
Concatenated count: 159540
Concatenated count: 159541
Concatenated count: 159542
Concatenated count: 159543
Concatenated count: 159544
Concatenated count: 159545
Concatenated count: 159546
Concatenated count: 159547
Concatenated count: 159548
Concatenated count: 159549
Concatenated count: 159550
Concatenated count: 159551
Concatenated count: 159552
Concatenated count: 159553
Concatenated count: 159554
Concatenated count: 159555
Concatenated count: 159556
Concatenated count: 159557
Concatenated count: 159558
Concatenated count: 159559
Concatenated count: 159560
Concatenated count: 159561
Concatenated count: 159562
Concatenated count: 159563
Concatenated count: 159564
C

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [47]:
print([(dictionary.get(tokenid),tfidf_value) for (tokenid,tfidf_value) in document_tfidf if tfidf_value > 0.03])

[('device', 0.030086460263501313), ('get', 0.05157388157368885), ('thing', 0.03350005119483402), ('much', 0.03052136402197972), ('still', 0.031147537370542506), ('work', 0.04722897564175468), ('also', 0.03584285770152653), ('make', 0.030780667181555123), ('one', 0.05163343763582788), ('great', 0.046412292359453974), ('card', 0.049187539380741385), ('touch', 0.03459980005827472), ('really', 0.04017376727928687), ('would', 0.04332347226164168), ('good', 0.05674331960629656), ('love', 0.04013156243632594), ('go', 0.031142754217928535), ('like', 0.05582319039862294), ('feature', 0.0436763275770873), ('first', 0.03174615936947822), ('smart', 0.034759055106664785), ('back', 0.034975446442529715), ('buy', 0.03222232330202613), ('new', 0.04736193528392952), ('got', 0.03731342162487228), ('use', 0.051866259478334426), ('need', 0.03418245863560965), ('want', 0.03367609691771582), ('text', 0.05843373893076289), ('minute', 0.03423703723358627), ('day', 0.0482099269616274), ('plan', 0.0344867976724

In [42]:
print(tfidf)

TfidfModel(num_docs=1093393, num_nnz=41632789)
